## Song Collection
Altering the collection pipeline I used for Friendshipify.

In [88]:
import pandas as pd
import numpy as np
from secret import *
import json
from IPython.display import clear_output

import spotipy
import spotipy.util as util
import spotipy.oauth2 as oauth2
client_credentials_manager = SpotifyClientCredentials(client_id=spotify_credentials['client_id'],
                                                      client_secret=spotify_credentials['client_secret'])

sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager)

token = credentials.get_access_token()

if token:
    sp = spotipy.Spotify(auth=token)
    print("Token Granted")
    
else:
    print("No token")


import psycopg2 as pg
conn = pg.connect(database=sql_credentials['database'],
                  user=sql_credentials['user'], 
                  password=sql_credentials['password'],
                  host=sql_credentials['host'])

def run_query(q):
    with conn:
        try:
            cur = conn.cursor()
            cur.execute(q)
            return pd.read_sql(q, conn)

        except (Exception, pg.DatabaseError) as error:
            print(error)

def run_command(c):
    with conn:
        try:
            cur = conn.cursor()
            cur.execute(c)
            cur.close()
            conn.commit()
            
        except (Exception, pg.DatabaseError) as error:
            print(error)

C:\Users\deand\Anaconda3\lib\site-packages\ipykernel_launcher.py:50: DeprecationWarning: You're using 'as_dict = True'.get_access_token will return the token string directly in future versions. Please adjust your code accordingly, or use get_cached_token instead.


Token Granted


### Categories

In [61]:
category_ids = ['toplists','in_the_car','pop','hiphop','mood','decades','country','rock','latin','focus','chill','edm_dance','rnb','indie_alt',
                'roots','party','classical','jazz','soul','romance','kpop','metal','reggae','blues','punk','funk','sessions']

single_playlists = ['37i9dQZF1DWTLSN7iG21yC','37i9dQZF1DX8CopunbDxgW','37i9dQZF1DX0b1hHYQtJjp','37i9dQZF1DX0BxHamIEkKV',
                   '37i9dQZF1DWTQwRw56TKNc','37i9dQZF1DWY0DyDKedRYY']

def get_playlist_tracks(playlist_id):
    results = sp.playlist_tracks(playlist_id)
    tracks = results['items']
    while results['next']:
        results = sp.next(results)
        tracks.extend(results['items'])
    return tracks

library = {}
for c in category_ids:
    results = sp.category_playlists(category_id=c, country='US', limit=50, offset=0)
    playlists = results['playlists']['items']

    playlist_ids = [p['id'] for p in playlists]

    playlist_tracks = []
    for q in playlist_ids:
        r = get_playlist_tracks(q)
        playlist_tracks.extend(r)
        
    library[c] = playlist_tracks
    
library.keys()

retrying ...1secs
retrying ...1secs
retrying ...1secs
retrying ...1secs


dict_keys(['toplists', 'in_the_car', 'pop', 'hiphop', 'mood', 'decades', 'country', 'rock', 'latin', 'focus', 'chill', 'edm_dance', 'rnb', 'indie_alt', 'roots', 'party', 'classical', 'jazz', 'soul', 'romance', 'kpop', 'metal', 'reggae', 'blues', 'punk', 'funk', 'sessions'])

In [66]:
all_tracks = {}

failed = 0
for k in library.keys():
    for t in library[k]:
        try:
            track_id = t['track']['id']
            track_name = t['track']['name']
            artist = t['track']['artists'][0]['name']
            artist_id = t['track']['artists'][0]['id']
            track_album_album_type = t['track']['album']['album_type']
            track_album_id = t['track']['album']['id']
            track_album_name = t['track']['album']['name']
            track_duration_ms = t['track']['duration_ms']
            track_popularity = t['track']['popularity']
            track_preview_url = t['track']['preview_url']
            subgenres = np.nan
            genre = k
            top_genre = np.nan

            all_tracks[track_id] = [track_name, artist, artist_id, track_album_album_type,
                                    track_album_id, track_album_name, track_duration_ms,
                                    track_popularity, track_preview_url, subgenres, genre,
                                    top_genre]

        except TypeError:
            failed += 1
            pass
        

print(len(all_tracks), failed)

test_df = pd.json_normalize(all_tracks)
test_df = test_df.transpose().reset_index()

df2 = pd.DataFrame(test_df[0].to_list(), columns=['track_name', 'artist', 'artist_id', 'track_album_album_type',
                                    'track_album_id', 'track_album_name', 'track_duration_ms',
                                    'track_popularity', 'track_preview_url', 'subgenres', 'genre',
                                    'top_genre'])

df2.insert(0,'track_id',test_df['index'])

df2

56981 63


track_id  \
0      3tjFYV6RSFtuktYl3ZtYcq   
1      5u1n1kITHCxxp8twBcZxWy   
2      02kDW379Yfd5PzW5A6vuGt   
3      45bE4HXI0AwGZXfZtMp8JR   
4      4wosxLl0mAqhneDzya2MfY   
...                       ...   
56976  090gEfL7wne6oBBDcrjjXN   
56977  6kHjDLcuhflKPU74beHnsv   
56978  71KsSsEJTuCwjV3Tqv9Z7Q   
56979  5diMiGvhafN0N2gYbXVJh5   
56980  52sj1c5u86DAiPvnQMAPCO   

                                              track_name          artist  \
0                                 Mood (feat. Iann Dior)        24kGoldn   
1                         Holy (feat. Chance The Rapper)   Justin Bieber   
2                                               Lemonade  Internet Money   
3                                     you broke me first      Tate McRae   
4                              Head & Heart (feat. MNEK)      Joel Corry   
...                                                  ...             ...   
56976  I’ve Got A Feeling - Recorded At Abbey Road St...  Paul McCartney   
56977  One After 909 - Recorded At Abbey Road Studios...  Paul McCartney   
56978  Nineteen Hundred And Eighty Five - Recorded At...  Paul McCartney   
56979  My Valentine - Recorded At Abbey Road Studios,...  Paul McCartney   
56980  Come On To Me - Recorded At Abbey Road Studios...  Paul McCartney   

                    artist_id track_album_album_type          track_album_id  \
0      6fWVd57NKTalqvmjRd2t8Z                 single  4YMnOf4a7obOcN1Gy2QEuM   
1      1uNFoZAHBGtllmzznpCI3s                 single  4hR7jjsPvRwwcHx8ntJSQS   
2      6MPCFvOQv5cIGfw3jODMF0                 single  1pFaEu56zqpzSviJc3htZN   
3      45dkTj5sMRSjrmBSBeiHym                 single  1RWiRfdNZKDe8VXzzf2VEc   
4      6DgP9otnZw5z6daOntINxp                 single  4w554Y1ts3lmzhn7hpfLBJ   
...                       ...                    ...                     ...   
56976  4STHEaNw4mPZ2tzheohgXB                  album  7piDt78gLATzAQv5JtQ4I7   
56977  4STHEaNw4mPZ2tzheohgXB                  album  7piDt78gLATzAQv5JtQ4I7   
56978  4STHEaNw4mPZ2tzheohgXB                  album  7piDt78gLATzAQv5JtQ4I7   
56979  4STHEaNw4mPZ2tzheohgXB                  album  7piDt78gLATzAQv5JtQ4I7   
56980  4STHEaNw4mPZ2tzheohgXB                  album  7piDt78gLATzAQv5JtQ4I7   

                                track_album_name  track_duration_ms  \
0                         Mood (feat. Iann Dior)             140525   
1                                           Holy             212093   
2      Lemonade (feat. Gunna, Don Toliver & NAV)             195428   
3                             you broke me first             169265   
4                      Head & Heart (feat. MNEK)             166028   
...                                          ...                ...   
56976    Spotify Singles: Paul McCartney Box Set             325358   
56977    Spotify Singles: Paul McCartney Box Set             173456   
56978    Spotify Singles: Paul McCartney Box Set             238240   
56979    Spotify Singles: Paul McCartney Box Set             187766   
56980    Spotify Singles: Paul McCartney Box Set             255480   

       track_popularity                                  track_preview_url  \
0                   100  https://p.scdn.co/mp3-preview/45cb08fdb67744ab...   
1                    92                                               None   
2                    93                                               None   
3                    94  https://p.scdn.co/mp3-preview/47afb10323067e82...   
4                    76                                               None   
...                 ...                                                ...   
56976                24                                               None   
56977                22                                               None   
56978                25                                               None   
56979                23                                               None   
56980                24                

In [67]:
single_playlists = ['37i9dQZF1DWTLSN7iG21yC','37i9dQZF1DX8CopunbDxgW','37i9dQZF1DX0b1hHYQtJjp','37i9dQZF1DX0BxHamIEkKV',
                   '37i9dQZF1DWTQwRw56TKNc','37i9dQZF1DWY0DyDKedRYY']

def get_playlist_tracks(playlist_id):
    results = sp.playlist_tracks(playlist_id)
    tracks = results['items']
    while results['next']:
        results = sp.next(results)
        tracks.extend(results['items'])
    return tracks


extra_tracks = []
for playlist in single_playlists:
    results = get_playlist_tracks(playlist)
    extra_tracks.extend(results)
extra_tracks

[{'added_at': '2020-08-12T17:29:10Z',
  'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/'},
   'href': 'https://api.spotify.com/v1/users/',
   'id': '',
   'type': 'user',
   'uri': 'spotify:user:'},
  'is_local': False,
  'primary_color': None,
  'track': {'album': {'album_type': 'single',
    'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/6WY7D3jk8zTrHtmkqqo5GI'},
      'href': 'https://api.spotify.com/v1/artists/6WY7D3jk8zTrHtmkqqo5GI',
      'id': '6WY7D3jk8zTrHtmkqqo5GI',
      'name': 'Maren Morris',
      'type': 'artist',
      'uri': 'spotify:artist:6WY7D3jk8zTrHtmkqqo5GI'},
     {'external_urls': {'spotify': 'https://open.spotify.com/artist/2FXC3k01G6Gw61bmprjgqS'},
      'href': 'https://api.spotify.com/v1/artists/2FXC3k01G6Gw61bmprjgqS',
      'id': '2FXC3k01G6Gw61bmprjgqS',
      'name': 'Hozier',
      'type': 'artist',
      'uri': 'spotify:artist:2FXC3k01G6Gw61bmprjgqS'}],
    'available_markets': ['AD',
     'AE',
  

In [72]:
all_tracks = {}

failed = 0

for t in extra_tracks:
    try:
        track_id = t['track']['id']
        track_name = t['track']['name']
        artist = t['track']['artists'][0]['name']
        artist_id = t['track']['artists'][0]['id']
        track_album_album_type = t['track']['album']['album_type']
        track_album_id = t['track']['album']['id']
        track_album_name = t['track']['album']['name']
        track_duration_ms = t['track']['duration_ms']
        track_popularity = t['track']['popularity']
        track_preview_url = t['track']['preview_url']
        subgenres = np.nan
        genre = k
        top_genre = np.nan

        all_tracks[track_id] = [track_name, artist, artist_id, track_album_album_type,
                                track_album_id, track_album_name, track_duration_ms,
                                track_popularity, track_preview_url, subgenres, genre,
                                top_genre]

    except TypeError:
        failed += 1
        pass
        

print(len(all_tracks), failed)

norm_df = pd.json_normalize(all_tracks)
norm_df = norm_df.transpose().reset_index()

df = pd.DataFrame(norm_df[0].to_list(), columns=['track_name', 'artist', 'artist_id', 'track_album_album_type',
                                    'track_album_id', 'track_album_name', 'track_duration_ms',
                                    'track_popularity', 'track_preview_url', 'subgenres', 'genre',
                                    'top_genre'])

df.insert(0,'track_id',norm_df['index'])

df

684 6


track_id                       track_name         artist  \
0    1yTTMcUhL7rtz08Dsgb7Qb          The Bones - with Hozier   Maren Morris   
1    7ce20yLkzuXXLUhzIDoZih                    Before You Go  Lewis Capaldi   
2    0d2iYfpKoM0QCKvcLCkBao  Eastside (with Halsey & Khalid)   benny blanco   
3    21jGcNKet2qwijlDFuPiPb                          Circles    Post Malone   
4    70eFcWOvlMObDhURTqT4Fv  Beautiful People (feat. Khalid)     Ed Sheeran   
..                      ...                              ...            ...   
679  6lwFOodKFZd0ro8bcIxlWg                   Princess Pouty      Ian Isiah   
680  1NK7206dmAh0RvB0GXUkqZ                  Five Miles High       New West   
681  0AUvWawuP0ibk4SQ3sIZjk                            Daisy       Ashnikko   
682  6CDzDgIUqeDY5g8ujExx2f                       Heat Waves  Glass Animals   
683  2pI0OyprOJssVYlqx9ZO3t                            Papás    Mau y Ricky   

                  artist_id track_album_album_type          track_album_id  \
0    6WY7D3jk8zTrHtmkqqo5GI                 single  6HzebUNgGlzC1AMBwHGIkH   
1    4GNC7GD6oZMSxPGyXy4MNB                 single  0488X5veBK6t3vSmIiTDJY   
2    5CiGnKThu5ctn9pBxv7DGa                 single  7pkLXlFdpQDfmHujT2AbBK   
3    246dkjvS1zLTtiykXe5h60                  album  4g1ZRSobMefqF6nelkgibi   
4    6eUKZXaKkcviH0Ku9w2n3V                  album  3oIFxDIo2fwuk4lwCmFZCx   
..                      ...                    ...                     ...   
679  0ldPEI4BOt8w3oBG9zhEPI                 single  30OuMUBR1zRI4cdHDhNo1z   
680  69bG9tC62d8oTFC9aTTosn                 single  54sGrSW0hk62Nl5XSHPmRD   
681  3PyJHH2wyfQK3WZrk9rpmP                 single  5tRhwDUyr3HypAaJysxUki   
682  4yvcSjfu4PC0CYQyLy4wSq                 single  69K1zrf6TkXHdYUO8n2qVi   
683  2wkoKEfS6dXwThbyTnZWFU                 single  1cvKWctA426nZjfP0DA2aA   

                    track_album_name  track_duration_ms  track_popularity  \
0            The Bones (with Hozier)             197298                77   
1                      Before You Go             215106                87   
2    Eastside (with Halsey & Khalid)             173799                80   
3               Hollywood's Bleeding             215280                90   
4        No.6 Collaborations Project             197866                78   
..                               ...                ...               ...   
679                   Princess Pouty             222640                40   
680                  Five Miles High             212924                50   
681                            Daisy             146523                84   
682                       Heat Waves             238805                76   
683                            Papás             193186                81   

                                     track_preview_url  subgenres     genre  \
0    https://p.scdn.co/mp3-preview/e05874f657064f79...        NaN  sessions   
1                                                 None        NaN  sessions   
2                                                 None        NaN  sessions   
3                                                 None        NaN  sessions   
4    https://p.scdn.co/mp3-preview/3ad904af9567a7c7...        NaN  sessions   
..                                                 ...        ...       ...   
679  https://p.scdn.co/mp3-preview/fbb515c14db2e1e2...        NaN  sessions   
680  https://p.scdn.co/mp3-preview/394ef00c2d0b4bd3...        NaN  sessions   
681  https://p.scdn.co/mp3-preview/b5b6b76fee422639...        NaN  sessions   
682                                               None        NaN  sessions   
683  https://p.scdn.co/mp3-preview/c0026b6e2c6eccea...        NaN  sessions   

     top_genre  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN  
..         ...  
679        NaN  
680        NaN  
681        NaN  
682        NaN  
683        NaN  

[684 rows x 13 columns]

In [75]:
all_df = df2.append(df, ignore_index=True)

len(all_df)

57665

In [76]:
username = 'deandraalvear'
scope = 'user-top-read'

token = util.prompt_for_user_token(username,
                                   scope,
                                   client_id,
                                   client_secret,
                                   redirect_uri)

if token:
    sp = spotipy.Spotify(auth=token)
    short_term = sp.current_user_top_tracks(limit=100, offset=0, time_range='short_term')
    medium_term = sp.current_user_top_tracks(limit=100, offset=0, time_range='medium_term')
    long_term = sp.current_user_top_tracks(limit=100, offset=0, time_range='long_term')
else:
    print("Can't get token for", username)
    
long_term



            User authentication requires interaction with your
            web browser. Once you enter your credentials and
            give authorization, you will be redirected to
            a url.  Paste that url you were directed to to
            complete the authorization.

        
Opened https://accounts.spotify.com/authorize?client_id=b05f690e17ba4b758d92a214cfbc7f24&response_type=code&redirect_uri=http%3A%2F%2F127.0.0.1&scope=user-top-read in your browser


Enter the URL you were redirected to: https://accounts.spotify.com/authorize?client_id=b05f690e17ba4b758d92a214cfbc7f24&response_type=code&redirect_uri=http%3A%2F%2F127.0.0.1&scope=user-top-read




            User authentication requires interaction with your
            web browser. Once you enter your credentials and
            give authorization, you will be redirected to
            a url.  Paste that url you were directed to to
            complete the authorization.

        
Opened https://accounts.spotify.com

{'items': [{'album': {'album_type': 'ALBUM',
    'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/18Zv2g2vUcEGqJf6WnjfXN'},
      'href': 'https://api.spotify.com/v1/artists/18Zv2g2vUcEGqJf6WnjfXN',
      'id': '18Zv2g2vUcEGqJf6WnjfXN',
      'name': 'Brandon Flowers',
      'type': 'artist',
      'uri': 'spotify:artist:18Zv2g2vUcEGqJf6WnjfXN'}],
    'available_markets': ['AD',
     'AE',
     'AR',
     'AT',
     'AU',
     'BE',
     'BG',
     'BH',
     'BO',
     'BR',
     'CA',
     'CH',
     'CL',
     'CO',
     'CR',
     'CY',
     'CZ',
     'DE',
     'DK',
     'DO',
     'DZ',
     'EC',
     'EE',
     'EG',
     'ES',
     'FI',
     'FR',
     'GR',
     'GT',
     'HK',
     'HN',
     'HU',
     'ID',
     'IL',
     'IN',
     'IS',
     'IT',
     'JO',
     'JP',
     'KW',
     'LB',
     'LI',
     'LT',
     'LU',
     'LV',
     'MA',
     'MC',
     'MT',
     'MX',
     'MY',
     'NI',
     'NL',
     'NO',
     'NZ',
     'OM'

In [87]:
len(medium_term['items'])

50

In [89]:
long_term['items'].extend(medium_term['items'])
len(my_tracks['items'])

TypeError: 'NoneType' object is not subscriptable

In [80]:
def generate_df(json_object):
    my_tracks = {}

    failed = 0

    for t in json_object:
        try:
            track_id = t['id']
            track_name = t['name']
            artist = t['artists'][0]['name']
            artist_id = t['artists'][0]['id']
            track_album_album_type = t['album']['album_type']
            track_album_id = t['album']['id']
            track_album_name = t['album']['name']
            track_duration_ms = t['duration_ms']
            track_popularity = t['popularity']
            track_preview_url = t['preview_url']
            subgenres = np.nan
            genre = np.nan
            top_genre = np.nan

            my_tracks[track_id] = [track_name, artist, artist_id, track_album_album_type,
                                    track_album_id, track_album_name, track_duration_ms,
                                    track_popularity, track_preview_url, subgenres, genre,
                                    top_genre]

        except TypeError:
            failed += 1
            pass


    print(len(my_tracks), failed)

    norm_df = pd.json_normalize(my_tracks)
    norm_df = norm_df.transpose().reset_index()

    my_tracks_df = pd.DataFrame(norm_df[0].to_list(), columns=['track_name', 'artist', 'artist_id', 'track_album_album_type',
                                        'track_album_id', 'track_album_name', 'track_duration_ms',
                                        'track_popularity', 'track_preview_url', 'subgenres', 'genre',
                                        'top_genre'])

    my_tracks_df.insert(0,'track_id',norm_df['index'])

    return my_tracks_df

In [95]:
long_term_df = generate_df(long_term)
medium_term_df = generate_df(medium_term)
short_term_df = generate_df(short_term)


print(len(long_term_df), len(medium_term_df), len(short_term_df))

97 0
50 0
50 0
97 50 50


In [96]:
my_tracks = long_term_df.append(medium_term_df, ignore_index=True)

my_tracks = my_tracks.append(short_term_df, ignore_index=True)

my_tracks

track_id  \
0    7B04VRtTs6ucHp8qJ6Nz8M   
1    0ofHAoxe9vBkTCp2UQIavz   
2    0tZZaTsZ6w8glKpgWiChGn   
3    6aBUnkXuCEQQHAlTokv9or   
4    6HKx5ERVgH7NYmYo9iAlMH   
..                      ...   
192  2Cu5ExXidcoE4vF5hIYict   
193  4BMbD4jHKpmukraBqxUWKJ   
194  4SGq9U1DXZfxnVyTxpCOuk   
195  1YaBa6DI8Suh02EtIZOpdM   
196  4SsWVvNKAHJP1T2bP6d2ut   

                                            track_name           artist  \
0                                          Lonely Town  Brandon Flowers   
1                               Dreams - 2004 Remaster    Fleetwood Mac   
2                                             The Club            Hinds   
3    This Must Be the Place (Naive Melody) - 2005 R...    Talking Heads   
4                                Angel - 2015 Remaster    Fleetwood Mac   
..                                                 ...              ...   
192                                     Heart to Break       Kim Petras   
193                              Fan Mail - Remastered          Blondie   
194                              Chance (Forever Love)      Angel Olsen   
195                                        Los Angeles             HAIM   
196                                  New Love Cassette      Angel Olsen   

                  artist_id track_album_album_type          track_album_id  \
0    18Zv2g2vUcEGqJf6WnjfXN                  ALBUM  0yCqicy5tGkPiB6gUZCRy4   
1    08GQAI4eElDnROBrJRGE0X                  ALBUM  0BwWUstDMUbgq2NYONRqlu   
2    4piFCokRN13muTud5Y2lhz                  ALBUM  4Bk5MyslUoXx6L58oQPA0l   
3    2x9SpqnPi8rlE9pjHBwmSC                  ALBUM  4sLCQxMRfn3gAHrBNZtbTH   
4    08GQAI4eElDnROBrJRGE0X                  ALBUM  5FIN8pyPVx8ggNs5jQ86Re   
..                      ...                    ...                     ...   
192  3Xt3RrJMFv5SZkCfUE8C1J                 SINGLE  4HbNtklEO6XJv638wZ1MZg   
193  4tpUmLEVLCGFr93o8hFFIB                  ALBUM  0N12rQBwFaD13ELCuEmUDl   
194  6mKqFxGMS5TGDZI3XkT5Rt                  ALBUM  6j4BnZet4BZ8YgSUZ3n1cf   
195  4Ui2kfOqGujY81UcPrb5KE                  ALBUM  4qNGDMsRNqDQZPkTWyyeRF   
196  6mKqFxGMS5TGDZI3XkT5Rt                  ALBUM  0RedX0LZkGUFoRwFntAaI0   

                         track_album_name  track_duration_ms  \
0                      The Desired Effect             210693   
1                  Rumours (Super Deluxe)             257800   
2                             I Don't Run             197373   
3    Speaking in Tongues (Deluxe Version)             296146   
4                    Tusk (2015 Remaster)             294053   
..                                    ...                ...   
192                        Heart to Break             225972   
193                       Plastic Letters             158800   
194                        Whole New Mess             329186   
195                Women In Music Pt. III             200000   
196                           All Mirrors             206413   

     track_popularity                                  track_preview_url  \
0                  46  https://p.scdn.co/mp3-preview/f5b7636eefe77137...   
1                  82  https://p.scdn.co/mp3-preview/40d1f6d82f16b05b...   
2                  31  https://p.scdn.co/mp3-preview/cff4e0a43f0a2ddf...   
3                  71  https://p.scdn.co/mp3-preview/1d52cb06bd5ac848...   
4                  38  https://p.scdn.co/mp3-preview/af9711b1c8195cee...   
..                ...                                                ...   
192                65  https://p.scdn.co/mp3-preview/7831b3dea79fdf8f...   
193                32  https://p.scdn.co/mp3-preview/fdfbb955f2a38b8f...   
194                44  https://p.scdn.co/mp3-preview/12f5f7d74e058c6e...   
195                54  https://p.scdn.co/mp3-preview/a36e13aae6bea7ce...   
196                58  https://p.scdn.co/mp3-preview/d75ccf98fd8ce989...   

     subgenres     genre  top_genre  
0          NaN  sessions        NaN  
1          NaN  sessions        NaN  
2          N

In [98]:
all_tracks = all_df.append(my_tracks, ignore_index=True)
all_tracks

track_id                      track_name          artist  \
0      3tjFYV6RSFtuktYl3ZtYcq          Mood (feat. Iann Dior)        24kGoldn   
1      5u1n1kITHCxxp8twBcZxWy  Holy (feat. Chance The Rapper)   Justin Bieber   
2      02kDW379Yfd5PzW5A6vuGt                        Lemonade  Internet Money   
3      45bE4HXI0AwGZXfZtMp8JR              you broke me first      Tate McRae   
4      4wosxLl0mAqhneDzya2MfY       Head & Heart (feat. MNEK)      Joel Corry   
...                       ...                             ...             ...   
57857  2Cu5ExXidcoE4vF5hIYict                  Heart to Break      Kim Petras   
57858  4BMbD4jHKpmukraBqxUWKJ           Fan Mail - Remastered         Blondie   
57859  4SGq9U1DXZfxnVyTxpCOuk           Chance (Forever Love)     Angel Olsen   
57860  1YaBa6DI8Suh02EtIZOpdM                     Los Angeles            HAIM   
57861  4SsWVvNKAHJP1T2bP6d2ut               New Love Cassette     Angel Olsen   

                    artist_id track_album_album_type          track_album_id  \
0      6fWVd57NKTalqvmjRd2t8Z                 single  4YMnOf4a7obOcN1Gy2QEuM   
1      1uNFoZAHBGtllmzznpCI3s                 single  4hR7jjsPvRwwcHx8ntJSQS   
2      6MPCFvOQv5cIGfw3jODMF0                 single  1pFaEu56zqpzSviJc3htZN   
3      45dkTj5sMRSjrmBSBeiHym                 single  1RWiRfdNZKDe8VXzzf2VEc   
4      6DgP9otnZw5z6daOntINxp                 single  4w554Y1ts3lmzhn7hpfLBJ   
...                       ...                    ...                     ...   
57857  3Xt3RrJMFv5SZkCfUE8C1J                 SINGLE  4HbNtklEO6XJv638wZ1MZg   
57858  4tpUmLEVLCGFr93o8hFFIB                  ALBUM  0N12rQBwFaD13ELCuEmUDl   
57859  6mKqFxGMS5TGDZI3XkT5Rt                  ALBUM  6j4BnZet4BZ8YgSUZ3n1cf   
57860  4Ui2kfOqGujY81UcPrb5KE                  ALBUM  4qNGDMsRNqDQZPkTWyyeRF   
57861  6mKqFxGMS5TGDZI3XkT5Rt                  ALBUM  0RedX0LZkGUFoRwFntAaI0   

                                track_album_name  track_duration_ms  \
0                         Mood (feat. Iann Dior)             140525   
1                                           Holy             212093   
2      Lemonade (feat. Gunna, Don Toliver & NAV)             195428   
3                             you broke me first             169265   
4                      Head & Heart (feat. MNEK)             166028   
...                                          ...                ...   
57857                             Heart to Break             225972   
57858                            Plastic Letters             158800   
57859                             Whole New Mess             329186   
57860                     Women In Music Pt. III             200000   
57861                                All Mirrors             206413   

       track_popularity                                  track_preview_url  \
0                   100  https://p.scdn.co/mp3-preview/45cb08fdb67744ab...   
1                    92                                               None   
2                    93                                               None   
3                    94  https://p.scdn.co/mp3-preview/47afb10323067e82...   
4                    76                                               None   
...                 ...                                                ...   
57857                65  https://p.scdn.co/mp3-preview/7831b3dea79fdf8f...   
57858                32  https://p.scdn.co/mp3-preview/fdfbb955f2a38b8f...   
57859                44  https://p.scdn.co/mp3-preview/12f5f7d74e058c6e...   
57860                54  https://p.scdn.co/mp3-preview/a36e13aae6bea7ce...   
57861                58  https://p.scdn.co/mp3-preview/d75ccf98fd8ce989...   

       subgenres     genre  top_genre  
0            NaN     party        NaN  
1            NaN   romance        NaN  
2            NaN    hiphop        NaN  
3            NaN   romance        NaN  
4            NaN     party        NaN  
...          ...       ...        ...  
57857        NaN 

In [99]:
all_tracks.to_csv('../data/all_tracks_df.csv', sep=";", index=False)

### Get all songs by all artists

Artist --> Album --> Album Tracks

In [3]:
all_tracks = pd.read_csv('../data/all_tracks_df.csv', delimiter=";")
all_tracks.head()

track_id                      track_name          artist  \
0  3tjFYV6RSFtuktYl3ZtYcq          Mood (feat. Iann Dior)        24kGoldn   
1  5u1n1kITHCxxp8twBcZxWy  Holy (feat. Chance The Rapper)   Justin Bieber   
2  02kDW379Yfd5PzW5A6vuGt                        Lemonade  Internet Money   
3  45bE4HXI0AwGZXfZtMp8JR              you broke me first      Tate McRae   
4  4wosxLl0mAqhneDzya2MfY       Head & Heart (feat. MNEK)      Joel Corry   

                artist_id track_album_album_type          track_album_id  \
0  6fWVd57NKTalqvmjRd2t8Z                 single  4YMnOf4a7obOcN1Gy2QEuM   
1  1uNFoZAHBGtllmzznpCI3s                 single  4hR7jjsPvRwwcHx8ntJSQS   
2  6MPCFvOQv5cIGfw3jODMF0                 single  1pFaEu56zqpzSviJc3htZN   
3  45dkTj5sMRSjrmBSBeiHym                 single  1RWiRfdNZKDe8VXzzf2VEc   
4  6DgP9otnZw5z6daOntINxp                 single  4w554Y1ts3lmzhn7hpfLBJ   

                            track_album_name  track_duration_ms  \
0                     Mood (feat. Iann Dior)             140525   
1                                       Holy             212093   
2  Lemonade (feat. Gunna, Don Toliver & NAV)             195428   
3                         you broke me first             169265   
4                  Head & Heart (feat. MNEK)             166028   

   track_popularity                                  track_preview_url  \
0               100  https://p.scdn.co/mp3-preview/45cb08fdb67744ab...   
1                92                                                NaN   
2                93                                                NaN   
3                94  https://p.scdn.co/mp3-preview/47afb10323067e82...   
4                76                                                NaN   

   subgenres    genre  top_genre  
0        NaN    party        NaN  
1        NaN  romance        NaN  
2        NaN   hiphop        NaN  
3        NaN  romance        NaN  
4        NaN    party        NaN

In [47]:
all_tracks = all_tracks[all_tracks['genre']!='classical']

In [67]:
result = sp.artist_top_tracks('3Xt3RrJMFv5SZkCfUE8C1J')
result['tracks']

[{'album': {'album_type': 'album',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/23fqKkggKUBHNkbKtXEls4'},
     'href': 'https://api.spotify.com/v1/artists/23fqKkggKUBHNkbKtXEls4',
     'id': '23fqKkggKUBHNkbKtXEls4',
     'name': 'Kygo',
     'type': 'artist',
     'uri': 'spotify:artist:23fqKkggKUBHNkbKtXEls4'}],
   'external_urls': {'spotify': 'https://open.spotify.com/album/7tcs1X9pzFvcLOPuhCstQJ'},
   'href': 'https://api.spotify.com/v1/albums/7tcs1X9pzFvcLOPuhCstQJ',
   'id': '7tcs1X9pzFvcLOPuhCstQJ',
   'images': [{'height': 640,
     'url': 'https://i.scdn.co/image/ab67616d0000b27380368f0aa8f90c51674f9dd2',
     'width': 640},
    {'height': 300,
     'url': 'https://i.scdn.co/image/ab67616d00001e0280368f0aa8f90c51674f9dd2',
     'width': 300},
    {'height': 64,
     'url': 'https://i.scdn.co/image/ab67616d0000485180368f0aa8f90c51674f9dd2',
     'width': 64}],
   'name': 'Golden Hour',
   'release_date': '2020-05-29',
   'release_date_precision'

In [75]:
len(tracks)

70779

In [89]:
from IPython.display import clear_output

artist_ids = all_tracks.loc[19885:,'artist_id'].unique()
l = len(artist_ids)

for i,artist in enumerate(artist_ids):
    result = sp.artist_top_tracks(artist)
    tracks.extend(result['tracks'])
    clear_output(wait=True)
    print(f"{i}/{l}")

18405/18406


In [86]:
len(tracks_1)

149966

In [87]:
tracks_2 = generate_df(tracks)
len(tracks_2)

210624 0


210624

In [90]:
tracks_3 = generate_df(tracks)
len(tracks_3)

213216 0


213216

In [91]:
tracks_3

track_id                                    track_name  \
0       3tjFYV6RSFtuktYl3ZtYcq                        Mood (feat. Iann Dior)   
1       27u7t9d7ZQoyjsCROHuZJ3                    Tick Tock (feat. 24kGoldn)   
2       6ap9lSRJ0iLriGLqoJ44cq                                CITY OF ANGELS   
3       6piAUJJQFD8oHDUr0b7l7q                                     VALENTINO   
4       68UW3plyDDNg1dkNIZRezJ      Tinted Eyes (feat. blackbear & 24kGoldn)   
...                        ...                                           ...   
213211  6jVVnTIC1zHFFdn2rBOE2g  This Must Be the Place (Naive Melody) - Live   
213212  3xJ8siSD7r5mDqLNtQ5CPf                              A Soft Seduction   
213213  6Mc0SvjQ2By4ZJWdF77M2C                             Dance on Vaseline   
213214  392cd1euczCOcZAs0SvvZS           The Last Emperor (Main Title Theme)   
213215  4MrwM9vGNeVKjIEtyZ2sQT                                  One Fine Day   

              artist               artist_id track_album_album_type  \
0           24kGoldn  6fWVd57NKTalqvmjRd2t8Z                 single   
1       Clean Bandit  6MDME20pz9RveH9rEXvrOM                 single   
2           24kGoldn  6fWVd57NKTalqvmjRd2t8Z                  album   
3           24kGoldn  6fWVd57NKTalqvmjRd2t8Z                  album   
4              DVBBS  5X4LWwbUFNzPkEas04uU82                 single   
...              ...                     ...                    ...   
213211   David Byrne  20vuBdFblWUo2FCOvUzusB                  album   
213212   David Byrne  20vuBdFblWUo2FCOvUzusB                  album   
213213   David Byrne  20vuBdFblWUo2FCOvUzusB                  album   
213214   David Byrne  20vuBdFblWUo2FCOvUzusB            compilation   
213215   David Byrne  20vuBdFblWUo2FCOvUzusB                  album   

                track_album_id                           track_album_name  \
0       4YMnOf4a7obOcN1Gy2QEuM                     Mood (feat. Iann Dior)   
1       3tuAs968COA2vxKjiLvmxr                 Tick Tock (feat. 24kGoldn)   
2       2eLpj5EDUhyAoTks8sxcKR                      DROPPED OUTTA COLLEGE   
3       2eLpj5EDUhyAoTks8sxcKR                      DROPPED OUTTA COLLEGE   
4       63qrRZqzJKieNXIbN2Uvkx   Tinted Eyes (feat. blackbear & 24kGoldn)   
...                        ...                                        ...   
213211  1F4G3aGUoFejTCLPQ4tTgh                       Live From Austin, TX   
213212  4tH7X5vlPeZclx8KNPNfE2                                   Feelings   
213213  4tH7X5vlPeZclx8KNPNfE2                                   Feelings   
213214  70iCI16xKlhPlJJT7OIKGH       The Last Emperor Original Soundtrack   
213215  0mqvus9jydETK3A63iIG09  Everything That Happens Will Happen Today   

        track_duration_ms  track_popularity  \
0                  140525               100   
1                  178373                86   
2                  112493                81   
3                  179133                80   
4                  175081                73   
...                   ...               ...   
213211             350586                42   
213212             181066                41   
213213             308026                40   
213214             241106                38   
213215             293640                37   

                                        track_preview_url  subgenres  genre  \
0       https://p.scdn.co/mp3-preview/45cb08fdb67744ab...        NaN    NaN   
1       https://p.scdn.co/mp3-preview/3d3f99ef7d4bea72...        NaN    NaN   
2       https://p.scdn.co/mp3-preview/72d1571034795d53...        NaN    NaN   
3       https://p.scdn.co/mp3-preview/6347fe20d7716220...        NaN    NaN   
4       https://p.scdn.co/mp3-preview/d198eb9b7ca39a5a...        NaN    NaN   
...                                                   ...        ...    ...   
213211  https://p.scdn.co/mp3-preview/98d44f14d88998fb...        NaN    NaN   
213212  https://p.scdn.co/mp3-preview/b8c46ccfdce6b555...        NaN    NaN   
213213 

In [92]:
tracks_3.to_csv('../data/all_tracks_df_V2.csv', sep=";", index=False)